# RecSys25-Demo

In the demo, we showcase the easy process of selecting the best-suited model in different scenarios with LensKit-Auto.
A LensKit-Auto developer simply has to call a single function call to select, tune and ensemble LensKit algorithms.

The demo is devided into two parts:

1. In the first part we are going to select and tune a Top-N recommender out of all of LensKit's algorithms on the Movielens 100k dataset.
3. In the second part we are going to tune and ensemble the BiasedMatrixFactorization predictor for the Movielens 100k dataset.

## Loading Data
First, we store the Movielens 100k dataset as a LensKit Dataset.

In [1]:
from lenskit.data import load_movielens

# read in the Movielens 100k dataset
ml100k = load_movielens('../data/ml-100k')
# convert to pandas dataframe to view the data
ratings = ml100k.interaction_table(format='pandas', original_ids=True)
ratings.head()

/home/anass/Desktop/ISG_OFF/testingpip/lenskit-auto/lktest/lib/python3.12/site-packages/lenskit/data/movielens.py:143: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  return pd.read_csv(
/home/anass/Desktop/ISG_OFF/testingpip/lenskit-auto/lktest/lib/python3.12/site-packages/lenskit/data/movielens.py:157: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  return pd.read_csv(


user_id  item_id  rating           timestamp
0        1        1     5.0 1997-09-22 22:02:38
1        1        2     3.0 1997-10-15 05:26:11
2        1        3     4.0 1997-11-03 07:42:40
3        1        4     3.0 1997-10-15 05:25:19
4        1        5     3.0 1998-03-13 01:15:12

## Splitting Data
For this demo we use a row-based holdout split. 25% of the dataset rows are  contained by the test set and 75% of the
rows are contained by the
train set. A holdout split is not ideal and we would rather use a cross-fold split in an experiment. But for the sake of
this demo, a holdout split keeps the code simple and we do not have to calculate the mean error over all folds.

In [2]:
from lenskit.splitting import sample_records

# perform holdout validation split using LensKit's splitting function
# Use 25% of interactions for test set
test_size = int(ml100k.interaction_count * 0.25)
split = sample_records(ml100k, size=test_size, rng=42)
train = split.train
test = split.test

## 1. Select and Tune a Recommender Model From LensKit
In the first part of our exeriment, we want to get the best performing recommender model on the Movielens 100k dataset. This model should be selected from all LensKit's algorihtms and tuned based on the *NDCG@10* metric .

A LensKit developer simply calls the *get_best_recommender_model()* function to select and optimize a LensKit model.

Note: To keep the demo easily executable, we reduced the search time from one hour to two minutes. Two minutes are enough to demonstrate how LensKit-Auto works. In a real use case, we provide more time for the optimization process.

In [3]:
import sys
sys.path.insert(0, '/home/anass/Desktop/ISG_OFF/testingpip/lenskit-auto')

from lkauto.lkauto import get_best_recommender_model

# call the get_best_recommender_model to automatically select and tune the best performing LensKit algorithm
optimized_model, configuration  = get_best_recommender_model(train=train, time_limit_in_sec=300)

2025-11-26 00:43:59,951 INFO ---Starting LensKit-Auto---
2025-11-26 00:43:59,952 INFO 	 optimization_time: 		 300 seconds
2025-11-26 00:43:59,952 INFO 	 num_evaluations: 			 500
2025-11-26 00:43:59,952 INFO 	 optimization_metric: 		 NDCG@10
2025-11-26 00:43:59,953 INFO 	 optimization_strategie: 	 bayesian
2025-11-26 00:43:59,953 INFO --Start Preprocessing--
2025-11-26 00:43:59,954 INFO --End Preprocessing--
2025-11-26 00:43:59,969 INFO --Start Bayesian Optimization--


[WARNING][target_function_runner.py:74] The argument budget is not set by SMAC: Consider removing it from the target function.
[WARNING][target_function_runner.py:74] The argument instance is not set by SMAC: Consider removing it from the target function.
[INFO][abstract_initial_design.py:139] Using 125 initial design configurations and 0 additional configurations.
[INFO][abstract_intensifier.py:307] Using only one seed for deterministic scenario.
[INFO][bias.py:109] building bias model for 56250 ratings
[INFO][bias.py:114] global mean: 3.527
[INFO][bias.py:135] computed biases for 1682 items
[INFO][bias.py:148] computed biases for 943 users


2025-11-26 00:44:08,096 INFO Run ID: 1 | ALSBiasedMF | NDCG@10: -0.6836117271148194


[INFO][implicit_evaler.py:216] Run ID: 1 | ALSBiasedMF | NDCG@10: -0.6836117271148194
[INFO][abstract_intensifier.py:517] Added config de577f as new incumbent because there are no incumbents yet.


/home/anass/Desktop/ISG_OFF/testingpip/lenskit-auto/lktest/lib/python3.12/site-packages/numpy/_core/fromnumeric.py:3860: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/home/anass/Desktop/ISG_OFF/testingpip/lenskit-auto/lktest/lib/python3.12/site-packages/numpy/_core/_methods.py:144: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
2025-11-26 00:44:08,116 INFO Run ID: 2 | Bias | NDCG@10: nan


...

[INFO][lkauto.py:428] {'algo': np.str_('ALSBiasedMF'), 'ALSBiasedMF:bias': np.False_, 'ALSBiasedMF:features': 386, 'ALSBiasedMF:ireg': 0.0329138819502, 'ALSBiasedMF:ureg': 0.0343698387582}


2025-11-26 00:46:40,605 INFO Saved model and incumbent to output/


[INFO][lkauto.py:433] Saved model and incumbent to output/


2025-11-26 00:46:40,605 INFO ---LensKit-Auto finished---


[INFO][lkauto.py:435] ---LensKit-Auto finished---


After this step, the LensKit developer uses the optimized model as any other LensKit model.
The following lines are copied from the *Running the Evaluation* part of the
[LensKit Getting Started Chapter](https://lkpy.readthedocs.io/en/stable/GettingStarted.html)

In [4]:
from lenskit.batch import recommend

recs = recommend(optimized_model, users=tuple(test.keys()), n=5, n_jobs=1)

In the last step of the evaluation, we use the LensKit Top-N RecListAnalysis object to compute the *NDCG@10* metric
for every user.

In [5]:
from lenskit.metrics import RunAnalysis, NDCG

# initialize analysis
analysis = RunAnalysis()
# add ndcg metric
analysis.add_metric(NDCG())
# evaluate recommendations against the test interactions
scores = analysis.measure(recs, test)
scores.list_metrics().head(8)

NDCG
user_id          
1        0.061407
2        0.124374
3        0.000000
4        0.000000
5        0.000000
6        0.110748
7        0.029571
8        0.272264

## 2. Tune and Ensemble a Predictor Model From LensKit
In the second part of this demo, we are going to tune and ensemble the *BiasedMatrixFactorization* algorithm with
LensKit-Auto. In comparison to the first part of the demo, we don't want to select an algorithm out of all LensKit
algorithms but tune a single predictor algorithm on the *RMSE* metric. Furthermore, we want to ensemble the best performing models to gain a
performance boost.

In this part of the demo we, need to create a configuration space that only contains the *BiasedMatrixFactorization*
algorithm.

Note: To keep the demo easily executable, we reduced the search time from one hour to two minutes. Two minutes are
enough to demonstrate how LensKit-Auto works. In a real use case, we provide more time for the
optimization process.

In [6]:
from ConfigSpace import Constant
from lkauto.algorithms.als import BiasedMF

# initialize BiasedMF ConfigurationSpace
cs = BiasedMF.get_default_configspace()
# declare, that the BiasedMF algorithm is the only algorithm contained in the configuration space
cs.add([Constant("algo", "ALSBiasedMF")])
# set a random seed for reproducible results
cs.seed(42)

In [7]:
from lkauto.lkauto import get_best_prediction_model
# Provide the BiasedMF ConfigurationSpace to the get_best_recommender_model function.
optimized_model, configuration = get_best_prediction_model(train=train, cs=cs, time_limit_in_sec=120)

2025-11-26 00:46:41,973 INFO ---Starting LensKit-Auto---
2025-11-26 00:46:41,973 INFO ---Starting LensKit-Auto---


[INFO][lkauto.py:133] ---Starting LensKit-Auto---


2025-11-26 00:46:41,975 INFO 	 optimization_time: 		 120 seconds
2025-11-26 00:46:41,975 INFO 	 optimization_time: 		 120 seconds


[INFO][lkauto.py:135] 	 optimization_time: 		 120 seconds


2025-11-26 00:46:41,976 INFO 	 num_evaluations: 			 500
2025-11-26 00:46:41,976 INFO 	 num_evaluations: 			 500


...

[INFO][lkauto.py:220] GES Ensemble Model


2025-11-26 00:48:44,505 INFO Saved model and incumbent to output/
2025-11-26 00:48:44,505 INFO Saved model and incumbent to output/


[INFO][lkauto.py:231] Saved model and incumbent to output/


2025-11-26 00:48:44,507 INFO ---LensKit-Auto finished---
2025-11-26 00:48:44,507 INFO ---LensKit-Auto finished---


[INFO][lkauto.py:233] ---LensKit-Auto finished---


After we have the optimized and ensembled *BiasedMatrixFactorization* models. We can use the ensemble like any other LensKit predictor model to get predictions.

In [8]:
#from lenskit.batch import predict
from lkauto.utils.pred_and_rec_functions import predict

preds = predict(optimized_model, test)

In the last step of this demo, we calculate the *RMSE* value for our optimized model.

In [9]:
from lenskit.metrics import RunAnalysis, RMSE

# initialize analysis
analysis = RunAnalysis()
# add rmse metric
analysis.add_metric(RMSE())
# evaluate predictions against the test data
scores = analysis.measure(preds, test)
# print the overall RMSE
print(f"RMSE: {scores.global_metrics()['RMSE']}")

RMSE: 0.9331948162389333
